In [1]:
import pandas as pd
import numpy as np 
import matplotlib.pyplot as plt
import tensorflow as tf
import pickle
from sklearn.linear_model import PassiveAggressiveClassifier
from sklearn.model_selection import train_test_split
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics import accuracy_score, confusion_matrix
from sklearn.manifold import TSNE
from scipy import spatial
from ast import literal_eval

In [2]:
# Import dataframe
df = pd.read_csv('./dataset/news_processed.csv')
df['text'] = df['text'].apply(literal_eval)
df['title'] = df['title'].apply(literal_eval)
df

title  \
0      [Donald, Trump, Sends, Embarrassing, New, Year...   
1      [Drunk, Bragging, Trump, Staffer, Started, Rus...   
2      [Sheriff, David, Clarke, Becomes, Internet, Jo...   
3      [Trump, Obsessed, Even, Obama, Name, Coded, We...   
4      [Pope, Francis, Called, Donald, Trump, Christm...   
...                                                  ...   
44273  [State, Department, says, ca, n't, find, email...   
44274             [P, PBS, Stand, Plutocratic, Pentagon]   
44275  [Anti-Trump, Protesters, Tools, Oligarchy, Inf...   
44276  [Ethiopia, Obama, seeks, progress, peace, secu...   
44277  [Jeb, Bush, Suddenly, Attacking, Trump, 's, Ma...   

                                                    text  label  
0      [Donald, Trump, wish, Americans, Happy, New, Y...      0  
1      [House, Intelligence, Committee, Chairman, Dev...      0  
2      [Friday, revealed, former, Milwaukee, Sheriff,...      0  
3      [Christmas, day, Donald, Trump, announced, wou...      0  
4      [Pope, Francis, used, annual, Christmas, Day, ...      0  
...                                                  ...    ...  
44273  [State, Department, told, Republican, National...      1  
44274  [P, PBS, Stand, Plutocratic, Pentagon, Posted,...      0  
44275  [Anti-Trump, Protesters, Tools, Oligarchy, Re...      0  
44276  [ADDIS, ABABA, Ethiopia, —President, Obama, co...      1  
44277  [Jeb, Bush, Suddenly, Attacking, Trump, 's, Ma...      1  

[44278 rows x 3 columns]

# Training the Model

## TF-IDF with Passive-Aggressive Classifier

In [36]:
# Mix title and text
df['content'] = df['title'] + df['text']

# Get training and test datasets
X_train, X_test, y_train, y_test = train_test_split(df['content'], df['label'], test_size=0.3, random_state=7)

In [37]:
X_train = X_train.apply(lambda x: ' '.join(x))
X_test = X_test.apply(lambda x: ' '.join(x))

In [38]:
# Use the TF-IDF Vectorizer to interpret words
tfidf_vectorizer = TfidfVectorizer(stop_words='english', max_df=0.7)
tfidf_train = tfidf_vectorizer.fit_transform(X_train)
tfidf_test = tfidf_vectorizer.transform(X_test)

#### Passive Aggressive Classifier

In [39]:
# Train the Passive Aggressive Classifier
pa_classifier = PassiveAggressiveClassifier(max_iter=50)
pa_classifier.fit(tfidf_train, y_train)

PassiveAggressiveClassifier(max_iter=50)

#### Predictions and Score

In [40]:
predictions = pa_classifier.predict(tfidf_test)
score = accuracy_score(y_test, predictions)
score

0.9568654019873533

In [41]:
confusion_matrix(y_test, predictions, labels=[0, 1])

array([[5881,  312],
       [ 261, 6830]])

#### Save the model

In [42]:
pickle.dump(pa_classifier, open('./models/pa_classifier.pkl', 'wb'))

## TF-IDF with Naive Bayes Classifier

In [94]:
# Mix title and text
df['content'] = df['title'] + df['text']

# Get training and test datasets
X_train, X_test, y_train, y_test = train_test_split(df['content'], df['label'], test_size=0.3, random_state=7)

In [95]:
# Make the elements of the arrays strings
X_train = list(map(str, X_train))
X_test = list(map(str, X_test))

In [96]:
# Use the TF-IDF Vectorizer to interpret words
tfidf_vectorizer = TfidfVectorizer(stop_words='english', max_df=0.7)
tfidf_train = tfidf_vectorizer.fit_transform(X_train)
tfidf_test = tfidf_vectorizer.transform(X_test)

#### Naive Bayes Classifier

In [97]:
from sklearn.naive_bayes import MultinomialNB

clf = MultinomialNB()
clf.fit(tfidf_train, y_train)

MultinomialNB()

#### Predictions and score

In [98]:
predictions = clf.predict(tfidf_test)
score = accuracy_score(y_test, predictions)
score

0.8921258657031015

In [99]:
confusion_matrix(y_test, predictions, labels=[0, 1])

array([[5201,  992],
       [ 441, 6650]])

#### Save the model

In [100]:
pickle.dump(clf, open('./models/naive_bayes.pkl', 'wb'))

## GloVe
https://medium.com/analytics-vidhya/basics-of-using-pre-trained-glove-vectors-in-python-d38905f356db

In [101]:
with open('./dataset/glove_data/glove.6B.50d.txt', 'r') as f:
    print(f.readline())
    print(f.readline())

the 0.418 0.24968 -0.41242 0.1217 0.34527 -0.044457 -0.49688 -0.17862 -0.00066023 -0.6566 0.27843 -0.14767 -0.55677 0.14658 -0.0095095 0.011658 0.10204 -0.12792 -0.8443 -0.12181 -0.016801 -0.33279 -0.1552 -0.23131 -0.19181 -1.8823 -0.76746 0.099051 -0.42125 -0.19526 4.0071 -0.18594 -0.52287 -0.31681 0.00059213 0.0074449 0.17778 -0.15897 0.012041 -0.054223 -0.29871 -0.15749 -0.34758 -0.045637 -0.44251 0.18785 0.0027849 -0.18411 -0.11514 -0.78581

, 0.013441 0.23682 -0.16899 0.40951 0.63812 0.47709 -0.42852 -0.55641 -0.364 -0.23938 0.13001 -0.063734 -0.39575 -0.48162 0.23291 0.090201 -0.13324 0.078639 -0.41634 -0.15428 0.10068 0.48891 0.31226 -0.1252 -0.037512 -1.5179 0.12612 -0.02442 -0.042961 -0.28351 3.5416 -0.11956 -0.014533 -0.1499 0.21864 -0.33412 -0.13872 0.31806 0.70358 0.44858 -0.080262 0.63003 0.32111 -0.46765 0.22786 0.36034 -0.37818 -0.56657 0.044691 0.30392



Above we can see what the glove pre-trained datasets contain.                       
Each word is associated with some vectors.
.......

In [3]:
embeddings_dict = {}

with open('./dataset/glove_data/glove.6B.100d.txt', 'r') as f:
    for line in f:
        values = line.split()
        word = values[0]
        vector = np.asarray(values[1:], "float32")
        embeddings_dict[word] = vector

#### Finding similar words

In [103]:
# Find similar vectors
def find_closest_embeddings(embedding):
    return sorted(embeddings_dict.keys(), key=lambda word: spatial.distance.euclidean(embeddings_dict[word], embedding))

In [104]:
# We can find the 5 closest words to the word passed
find_closest_embeddings(embeddings_dict["cat"])[:5]

['cat', 'dog', 'rabbit', 'cats', 'monkey']

#### Mathematical Operations

In [105]:
# We can also perform mathematical operations on the vectors and therefore find relationships to the words
print(find_closest_embeddings(
    embeddings_dict["england"] - embeddings_dict["london"] + embeddings_dict["rome"]
)[:5])

['italy', 'rome', 'england', 'roman', 'centuries']


#### Visualize the embeddings

We use the T-SNE (T-distributed Stochastic Neighbor Embedding) to reduce the dimensions of the word vectors to 2D

In [106]:
tsne = TSNE(n_components=2, random_state=0)
# List of words and the corresponding vectors
words =  list(embeddings_dict.keys())
vectors = [embeddings_dict[word] for word in words]

Y = tsne.fit_transform(vectors[:1000])

In [107]:
# We plot the result
plt.figure(figsize=(40, 30), dpi=300)
plt.scatter(Y[:, 0], Y[:, 1])

# We add the name of the word to each dot
for label, x, y in zip(words, Y[:, 0], Y[:, 1]):
    plt.annotate(label, xy=(x, y), xytext=(0, 0), textcoords="offset points")

plt.show()

### Prepare data

In [4]:
# Mix title and text
df['content'] = df['title'] + df['text']

# Get training and test datasets
X_train, X_test, y_train, y_test = train_test_split(df['content'], df['label'], test_size=0.3, random_state=7)

In [5]:
def to_vectors(data):
    M = []
    for w in data:
        try:
            M.append(embeddings_dict[w])
        except:
            continue
    M = np.array(M)
    v = M.sum(axis=0)
    if type(v) != np.ndarray:
        return np.zeros(100)
    return v / np.sqrt((v ** 2).sum())

In [6]:
from tqdm import tqdm


X_train = [to_vectors(x) for x in tqdm(X_train)]
X_test = [to_vectors(x) for x in tqdm(X_test)]

X_train = np.array(X_train)
X_test = np.array(X_test)

100%|██████████| 13284/13284 [00:05<00:00, 2265.69it/s]


## GloVe with Support Vector Machines

In [7]:
from sklearn.svm import SVC

svm_clf = SVC()
svm_clf.fit(X_train, y_train)

SVC()

#### Predictions and score

In [8]:
predictions = svm_clf.predict(X_test)
score = accuracy_score(y_test, predictions)
score

0.9122252333634447

In [9]:
confusion_matrix(y_test, predictions, labels=[0, 1])

array([[5550,  643],
       [ 523, 6568]])

#### Save model

In [32]:
pickle.dump(svm_clf, open('./models/svm.pkl', 'wb'))

### Train Final SVM Model

In [14]:
from sklearn.svm import SVC

X_data = df['content']
y_data = df['label']

def to_vectors(data):
    M = []
    for w in data:
        try:
            M.append(embeddings_dict[w])
        except:
            continue
    M = np.array(M)
    v = M.sum(axis=0)
    if type(v) != np.ndarray:
        return np.zeros(100)
    return v / np.sqrt((v ** 2).sum())


X_data = [to_vectors(x) for x in X_data]
X_data = np.array(X_data)

final_svm_clf = SVC()
final_svm_clf.fit(X_data, y_data)

SVC()

In [15]:
pickle.dump(final_svm_clf, open('./models/final_svm.pkl', 'wb'))

## GloVe with Neural Networks

In [4]:
# Mix title and text
df['content'] = df['title'] + df['text']

# Get training and test datasets
X_train, X_test, y_train, y_test = train_test_split(df['content'], df['label'], test_size=0.3, random_state=7)

In [5]:
max_features = 10000
maxlen = 300

In [6]:
from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.preprocessing.sequence import pad_sequences

tokenizer = Tokenizer(num_words=max_features)

# Training data
tokenizer.fit_on_texts(X_train)
tokenized_train = tokenizer.texts_to_sequences(X_train)
X_train = pad_sequences(tokenized_train, maxlen=maxlen)

# Test data
tokenizer.fit_on_texts(X_test)
tokenized_test = tokenizer.texts_to_sequences(X_test)
X_test = pad_sequences(tokenized_test, maxlen=maxlen)

all_embs = np.stack(embeddings_dict.values())
emb_mean, emb_std = all_embs.mean(), all_embs.std()
embed_size = all_embs.shape[1]


word_index = tokenizer.word_index
vocab_size = min(max_features, len(word_index))

embedding_matrix = np.random.normal(emb_mean, emb_std, (vocab_size, embed_size))

for word, i in word_index.items():
    if i >= max_features: 
        continue
    embedding_vector = embeddings_dict.get(word)
    if embedding_vector is not None:
        embedding_matrix[i] = embedding_vector

#### Build the model

In [185]:
from tensorflow.keras.layers import Embedding
from tensorflow.keras.layers import Dense, Embedding, LSTM, Dropout, Flatten
from tensorflow.keras.models import Sequential

model = Sequential()

model.add(Embedding(max_features, output_dim=embed_size, weights=[embedding_matrix], input_length=maxlen, trainable=False))
model.add(LSTM(units=embed_size, return_sequences=True, recurrent_dropout=0.25, dropout=0.5))
model.add(LSTM(units=64, recurrent_dropout=0.1, dropout=0.3))
model.add(Dense(16, activation='relu'))
model.add(Dense(1, activation='sigmoid'))

model.compile(
    optimizer='adam',
    loss='binary_crossentropy',
    metrics=['accuracy']
)

model.summary()

Model: "sequential_14"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
embedding_14 (Embedding)     (None, 300, 100)          1000000   
_________________________________________________________________
lstm_14 (LSTM)               (None, 300, 100)          80400     
_________________________________________________________________
lstm_15 (LSTM)               (None, 64)                42240     
_________________________________________________________________
dense_14 (Dense)             (None, 16)                1040      
_________________________________________________________________
dense_15 (Dense)             (None, 1)                 17        
Total params: 1,123,697
Trainable params: 123,697
Non-trainable params: 1,000,000
_________________________________________________________________


#### Train and evaluate the model

In [186]:
model.fit(X_train, y_train, epochs=10, validation_split=0.3)

loss, accuracy = model.evaluate(X_test, y_test)
print(f'Accuracy: {accuracy}\nLoss: {loss}')

Epoch 1/10
678/678 [==============================] - 695s 1s/step - loss: 0.4504 - accuracy: 0.7787 - val_loss: 0.3580 - val_accuracy: 0.8114
Epoch 2/10
678/678 [==============================] - 606s 894ms/step - loss: 0.3438 - accuracy: 0.8433 - val_loss: 0.2467 - val_accuracy: 0.8916
Epoch 3/10
678/678 [==============================] - 1892s 3s/step - loss: 0.2734 - accuracy: 0.8796 - val_loss: 0.2013 - val_accuracy: 0.9179
Epoch 4/10
678/678 [==============================] - 1994s 3s/step - loss: 0.2363 - accuracy: 0.8994 - val_loss: 0.2125 - val_accuracy: 0.9202
Epoch 5/10
678/678 [==============================] - 1457s 2s/step - loss: 0.2127 - accuracy: 0.9095 - val_loss: 0.2145 - val_accuracy: 0.9163
Epoch 6/10
678/678 [==============================] - 824s 1s/step - loss: 0.2482 - accuracy: 0.8984 - val_loss: 0.2087 - val_accuracy: 0.9219
Epoch 7/10
678/678 [==============================] - 1585s 2s/step - loss: 0.2149 - accuracy: 0.9129 - val_loss: 0.1594 - val_accuracy:

#### Save model

In [187]:
model.save('./models/nn.h5') 